In [0]:
 /FileStore/tables/Sales_SalesOrderDetail-3.csv

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.types import StructType, StructField, StringType, IntegerType, DoubleType, TimestampType
from pyspark.sql.functions import col, date_format, year, from_utc_timestamp, to_utc_timestamp

# Initialize Spark session
spark = SparkSession.builder.appName("DateTimeProcessing").getOrCreate()

# Define the schema using StructType and StructField
schema = StructType([
    StructField('SalesOrderID', IntegerType(), True),
    StructField('SalesOrderDetailID', IntegerType(), True),
    StructField('CarrierTrackingNumber', StringType(), True),
    StructField('OrderQty', IntegerType(), True),
    StructField('ProductID', IntegerType(), True),
    StructField('SpecialOfferID', IntegerType(), True),
    StructField('UnitPrice', DoubleType(), True),
    StructField('UnitPriceDiscount', DoubleType(), True),
    StructField('LineTotal', DoubleType(), True),
    StructField('rowguid', StringType(), True),
    StructField('ModifiedDate', TimestampType(), True)  # Changed to TimestampType
])

# Load the CSV data with the defined schema
df = spark.read.csv("/FileStore/tables/Sales_SalesOrderDetail-3.csv", schema=schema, header=True)

# Convert UTC to IST (Asia/Kolkata)
df_with_timezones = df.withColumn("ModifiedDate_UTC", to_utc_timestamp(col("ModifiedDate"), "UTC")) \
                      .withColumn("ModifiedDate_IST", from_utc_timestamp(col("ModifiedDate_UTC"), "Asia/Kolkata"))

# Extract year, time and add them to the DataFrame
df_processed = df_with_timezones.withColumn("Year", year(col("ModifiedDate"))) \
                                 .withColumn("Time", date_format(col("ModifiedDate"), "HH:mm:ss"))

# Select the required columns
df_result = df_processed.select(
    col("SalesOrderID"),
    col("Year"),
    col("Time"),
    col("ModifiedDate_UTC"),
    col("ModifiedDate_IST")
)

# Show the resulting DataFrame
df_result.show(truncate=False)


from pyspark.sql.functions import count

df_grouped = df_processed.groupBy("Year").agg(
    count("SalesOrderID").alias("TotalOrders")
)


# Show the resulting grouped DataFrame
df_grouped.show(truncate=False)

+------------+----+--------+-------------------+-------------------+
|SalesOrderID|Year|Time    |ModifiedDate_UTC   |ModifiedDate_IST   |
+------------+----+--------+-------------------+-------------------+
|43659       |2011|00:00:00|2011-05-31 00:00:00|2011-05-31 05:30:00|
|43659       |2011|00:00:00|2011-05-31 00:00:00|2011-05-31 05:30:00|
|43659       |2011|00:00:00|2011-05-31 00:00:00|2011-05-31 05:30:00|
|43659       |2011|00:00:00|2011-05-31 00:00:00|2011-05-31 05:30:00|
|43659       |2011|00:00:00|2011-05-31 00:00:00|2011-05-31 05:30:00|
|43659       |2011|00:00:00|2011-05-31 00:00:00|2011-05-31 05:30:00|
|43659       |2011|00:00:00|2011-05-31 00:00:00|2011-05-31 05:30:00|
|43659       |2011|00:00:00|2011-05-31 00:00:00|2011-05-31 05:30:00|
|43659       |2011|00:00:00|2011-05-31 00:00:00|2011-05-31 05:30:00|
|43659       |2011|00:00:00|2011-05-31 00:00:00|2011-05-31 05:30:00|
|43659       |2011|00:00:00|2011-05-31 00:00:00|2011-05-31 05:30:00|
|43660       |2011|00:00:00|2011-0

In [0]:
DAY LIGHT SAVING 

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.types import StructType, StructField, IntegerType, StringType, DoubleType, TimestampType

# Initialize the Spark session
spark = SparkSession.builder.appName("Timezone Conversion").getOrCreate()

# Define the schema
schema = StructType([
    StructField("SalesOrderID", IntegerType(), True),
    StructField("SalesOrderDetailID", IntegerType(), True),
    StructField("CarrierTrackingNumber", StringType(), True),
    StructField("OrderQty", IntegerType(), True),
    StructField("ProductID", IntegerType(), True),
    StructField("SpecialOfferID", IntegerType(), True),
    StructField("UnitPrice", DoubleType(), True),
    StructField("UnitPriceDiscount", DoubleType(), True),
    StructField("LineTotal", DoubleType(), True),
    StructField("rowguid", StringType(), True),
    StructField("ModifiedDate", TimestampType(), True)
])

# Load the CSV data with the defined schema
df = spark.read.format("csv").option("header", "true").schema(schema).load("/FileStore/tables/Sales_SalesOrderDetail.csv")

# Register the DataFrame as a temporary SQL view
df.createOrReplaceTempView("sales_data")


In [0]:
%sql
-- Show the first few rows of the sales_data table
SELECT * FROM sales_data LIMIT 10;


SalesOrderID SalesOrderDetailID CarrierTrackingNumber OrderQty ProductID SpecialOfferID UnitPrice UnitPriceDiscount LineTotal rowguid ModifiedDate 43659 2 4911-403C-98 3 777 1 2024.994 0.0 6074.982 7ABB600D-1E77-41BE-9FE5-B9142CFC08FA 2011-05-31T00:00:00.000+0000 43659 3 4911-403C-98 1 778 1 2024.994 0.0 2024.994 475CF8C6-49F6-486E-B0AD-AFC6A50CDD2F 2011-05-31T00:00:00.000+0000 43659 4 4911-403C-98 1 771 1 2039.994 0.0 2039.994 04C4DE91-5815-45D6-8670-F462719FBCE3 2011-05-31T00:00:00.000+0000 43659 5 4911-403C-98 1 772 1 2039.994 0.0 2039.994 5A74C7D2-E641-438E-A7AC-37BF23280301 2011-05-31T00:00:00.000+0000 43659 6 4911-403C-98 2 773 1 2039.994 0.0 4079.988 CE472532-A4C0-45BA-816E-EEFD3FD848B3 2011-05-31T00:00:00.000+0000 43659 7 4911-403C-98 1 774 1 2039.994 0.0 2039.994 80667840-F962-4EE3-96E0-AECA108E0D4F 2011-05-31T00:00:00.000+0000 43659 8 4911-403C-98 3 714 1 28.8404 0.0 86.5212 E9D54907-E7B7-4969-80D9-76BA69F8A836 2011-05-31T00:00:00.000+0000 43659 9 4911-403C-98 1 716 1 28.8404 0.0 28.8404 AA542630-BDCD-4CE5-89A0-C1BF82747725 2011-05-31T00:00:00.000+0000 43659 10 4911-403C-98 6 709 1 5.7 0.0 34.2 AC769034-3C2F-495C-A5A7-3B71CDB25D4E 2011-05-31T00:00:00.000+0000 43659 11 4911-403C-98 2 712 1 5.1865 0.0 10.373 06A66921-6B9F-4199-A912-DDAFD383472B 2011-05-31T00:00:00.000+0000

In [0]:
%sql
-- Step 2.1: Create a static timezone table
WITH time_zones AS (
    SELECT 'Europe/London' AS zone_id, 'BST' AS local_time_with_dst, 'GMT' AS local_time_without_dst UNION ALL
    SELECT 'Europe/Berlin', 'CEST', 'CET' UNION ALL
    SELECT 'Europe/Paris', 'CEST', 'CET' UNION ALL
    SELECT 'Europe/Madrid', 'CEST', 'CET' UNION ALL
    SELECT 'Europe/Rome', 'CEST', 'CET' UNION ALL
    SELECT 'Europe/Athens', 'EEST', 'EET'
)
SELECT * FROM time_zones;


zone_id local_time_with_dst local_time_without_dst Europe/London BST GMT Europe/Berlin CEST CET Europe/Paris CEST CET Europe/Madrid CEST CET Europe/Rome CEST CET Europe/Athens EEST EET

In [0]:
%sql
-- Step 2.2: Convert UTC timestamps to local time with and without DST, and determine DST status
WITH time_zones AS (
    SELECT 'Europe/London' AS zone_id, 'BST' AS local_time_with_dst, 'GMT' AS local_time_without_dst UNION ALL
    SELECT 'Europe/Berlin', 'CEST', 'CET' UNION ALL
    SELECT 'Europe/Paris', 'CEST', 'CET' UNION ALL
    SELECT 'Europe/Madrid', 'CEST', 'CET' UNION ALL
    SELECT 'Europe/Rome', 'CEST', 'CET' UNION ALL
    SELECT 'Europe/Athens', 'EEST', 'EET'
),
converted_times AS (
    SELECT
        sd.SalesOrderID,
        sd.SalesOrderDetailID,
        sd.CarrierTrackingNumber,
        sd.OrderQty,
        sd.ProductID,
        sd.SpecialOfferID,
        sd.UnitPrice,
        sd.UnitPriceDiscount,
        sd.LineTotal,
        sd.rowguid,
        sd.ModifiedDate,
        tz.zone_id,
        
        -- Convert to local time with DST
        from_utc_timestamp(sd.ModifiedDate, tz.zone_id) AS Local_Time_With_DST,
        
        -- Convert to local time without DST
        from_utc_timestamp(sd.ModifiedDate, tz.zone_id) AS Local_Time_Without_DST,
        
        -- Convert to IST
        from_utc_timestamp(sd.ModifiedDate, 'Asia/Kolkata') AS Local_Time_IST,
        
        -- Convert to UTC
        sd.ModifiedDate AS Local_Time_UTC,
        
        -- Calculate day of the year
        dayofyear(sd.ModifiedDate) AS Day_Of_Year,
        
        -- Determine DST status based on day of the year (assuming DST is between days 60 and 300)
        CASE 
            WHEN dayofyear(sd.ModifiedDate) BETWEEN 60 AND 300 THEN 'Yes'
            ELSE 'No'
        END AS Is_DST_On

    FROM sales_data sd
    CROSS JOIN time_zones tz
)

-- Show the final output
SELECT * FROM converted_times;


SalesOrderID SalesOrderDetailID CarrierTrackingNumber OrderQty ProductID SpecialOfferID UnitPrice UnitPriceDiscount LineTotal rowguid ModifiedDate zone_id Local_Time_With_DST Local_Time_Without_DST Local_Time_IST Local_Time_UTC Day_Of_Year Is_DST_On 43659 2 4911-403C-98 3 777 1 2024.994 0.0 6074.982 7ABB600D-1E77-41BE-9FE5-B9142CFC08FA 2011-05-31T00:00:00.000+0000 Europe/London 2011-05-31T01:00:00.000+0000 2011-05-31T01:00:00.000+0000 2011-05-31T05:30:00.000+0000 2011-05-31T00:00:00.000+0000 151 Yes 43659 2 4911-403C-98 3 777 1 2024.994 0.0 6074.982 7ABB600D-1E77-41BE-9FE5-B9142CFC08FA 2011-05-31T00:00:00.000+0000 Europe/Berlin 2011-05-31T02:00:00.000+0000 2011-05-31T02:00:00.000+0000 2011-05-31T05:30:00.000+0000 2011-05-31T00:00:00.000+0000 151 Yes 43659 2 4911-403C-98 3 777 1 2024.994 0.0 6074.982 7ABB600D-1E77-41BE-9FE5-B9142CFC08FA 2011-05-31T00:00:00.000+0000 Europe/Paris 2011-05-31T02:00:00.000+0000 2011-05-31T02:00:00.000+0000 2011-05-31T05:30:00.000+0000 2011-05-31T00:00:00.000+0000 151 Yes 43659 2 4911-403C-98 3 777 1 2024.994 0.0 6074.982 7ABB600D-1E77-41BE-9FE5-B9142CFC08FA 2011-05-31T00:00:00.000+0000 Europe/Madrid 2011-05-31T02:00:00.000+0000 2011-05-31T02:00:00.000+0000 2011-05-31T05:30:00.000+0000 2011-05-31T00:00:00.000+0000 151 Yes 43659 2 4911-403C-98 3 777 1 2024.994 0.0 6074.982 7ABB600D-1E77-41BE-9FE5-B9142CFC08FA 2011-05-31T00:00:00.000+0000 Europe/Rome 2011-05-31T02:00:00.000+0000 2011-05-31T02:00:00.000+0000 2011-05-31T05:30:00.000+0000 2011-05-31T00:00:00.000+0000 151 Yes 43659 2 4911-403C-98 3 777 1 2024.994 0.0 6074.982 7ABB600D-1E77-41BE-9FE5-B9142CFC08FA 2011-05-31T00:00:00.000+0000 Europe/Athens 2011-05-31T03:00:00.000+0000 2011-05-31T03:00:00.000+0000 2011-05-31T05:30:00.000+0000 2011-05-31T00:00:00.000+0000 151 Yes 43659 3 4911-403C-98 1 778 1 2024.994 0.0 2024.994 475CF8C6-49F6-486E-B0AD-AFC6A50CDD2F 2011-05-31T00:00:00.000+0000 Europe/London 2011-05-31T01:00:00.000+0000 2011-05-31T01:00:00.000+0000 2011-05-31T05:30:00.000+0000 2011-05-31T00:00:00.000+0000 151 Yes 43659 3 4911-403C-98 1 778 1 2024.994 0.0 2024.994 475CF8C6-49F6-486E-B0AD-AFC6A50CDD2F 2011-05-31T00:00:00.000+0000 Europe/Berlin 2011-05-31T02:00:00.000+0000 2011-05-31T02:00:00.000+0000 2011-05-31T05:30:00.000+0000 2011-05-31T00:00:00.000+0000 151 Yes 43659 3 4911-403C-98 1 778 1 2024.994 0.0 2024.994 475CF8C6-49F6-486E-B0AD-AFC6A50CDD2F 2011-05-31T00:00:00.000+0000 Europe/Paris 2011-05-31T02:00:00.000+0000 2011-05-31T02:00:00.000+0000 2011-05-31T05:30:00.000+0000 2011-05-31T00:00:00.000+0000 151 Yes 43659 3 4911-403C-98 1 778 1 2024.994 0.0 2024.994 475CF8C6-49F6-486E-B0AD-AFC6A50CDD2F 2011-05-31T00:00:00.000+0000 Europe/Madrid 2011-05-31T02:00:00.000+0000 2011-05-31T02:00:00.000+0000 2011-05-31T05:30:00.000+0000 2011-05-31T00:00:00.000+0000 151 Yes 43659 3 4911-403C-98 1 778 1 2024.994 0.0 2024.994 475CF8C6-49F6-486E-B0AD-AFC6A50CDD2F 2011-05-31T00:00:00.000+0000 Europe/Rome 2011-05-31T02:00:00.000+0000 2011-05-31T02:00:00.000+0000 2011-05-31T05:30:00.000+0000 2011-05-31T00:00:00.000+0000 151 Yes 43659 3 4911-403C-98 1 778 1 2024.994 0.0 2024.994 475CF8C6-49F6-486E-B0AD-AFC6A50CDD2F 2011-05-31T00:00:00.000+0000 Europe/Athens 2011-05-31T03:00:00.000+0000 2011-05-31T03:00:00.000+0000 2011-05-31T05:30:00.000+0000 2011-05-31T00:00:00.000+0000 151 Yes 43659 4 4911-403C-98 1 771 1 2039.994 0.0 2039.994 04C4DE91-5815-45D6-8670-F462719FBCE3 2011-05-31T00:00:00.000+0000 Europe/London 2011-05-31T01:00:00.000+0000 2011-05-31T01:00:00.000+0000 2011-05-31T05:30:00.000+0000 2011-05-31T00:00:00.000+0000 151 Yes 43659 4 4911-403C-98 1 771 1 2039.994 0.0 2039.994 04C4DE91-5815-45D6-8670-F462719FBCE3 2011-05-31T00:00:00.000+0000 Europe/Berlin 2011-05-31T02:00:00.000+0000 2011-05-31T02:00:00.000+0000 2011-05-31T05:30:00.000+0000 2011-05-31T00:00:00.000+0000 151 Yes 43659 4 4911-403C-98 1 771 1 2039.994 0.0 2039.994 04C4DE91-5815-45D6-8670-F462719FBCE3 2011-05-31T00:00:00.000+0000 Europe/Paris 2011-05-31T02:00:00.000+0000 2011-05-31T02:00:00.000+000